In [24]:
import sys
sys.path.append("/Users/rohan/public_html/Hegemon")
import StepMiner as smn
import HegemonUtil as hu
import re
import numpy as np
import scipy
import io
from scipy import io
import math
import itertools
from itertools import combinations 
import matplotlib.pyplot as plt
%matplotlib inline
from matplotlib.backends.backend_pdf import PdfPages
import pandas as pd
import statsmodels.stats.proportion
import seaborn as sns
import scanpy as sc
import GEOparse
import pickle
with open('ensembl_to_genesymbol.pickle', 'rb') as handle:
     ensembl_to_genesymbol = pickle.load(handle)

In [20]:
# Read raw counts
df = pd.DataFrame(pd.read_csv('GSE165694_Dietschmann_et_al_raw_counts.txt', sep = '\t', header=0))
df.columns = ["ProbeID", "GSM5048309", "GSM5048310", "GSM5048311", "GSM5048312", "GSM5048313", "GSM5048314"]
df

ProbeID  GSM5048309  GSM5048310  GSM5048311  GSM5048312  \
0      ENSMUSG00000102693.1           0           0           0           0   
1      ENSMUSG00000064842.1           0           1           0           0   
2      ENSMUSG00000051951.5           0           0           0           0   
3      ENSMUSG00000102851.1           0           0           0           0   
4      ENSMUSG00000103377.1           0           0           0           0   
...                     ...         ...         ...         ...         ...   
55293  ENSMUSG00000095366.2          13          65          46         157   
55294  ENSMUSG00000095134.2           0           0           3           0   
55295  ENSMUSG00000096768.8         572         856         908        1323   
55296  ENSMUSG00000099871.1           0           0           0           0   
55297  ENSMUSG00000096850.1           0           0           0           0   

       GSM5048313  GSM5048314  
0               0           0  
1               0           0  
2               0           0  
3               0           0  
4               0           0  
...           ...         ...  
55293         276          26  
55294           0           0  
55295         832         553  
55296           0           0  
55297           0           0  

[55298 rows x 7 columns]

In [39]:
expr = df.copy(deep=True)
expr = expr.drop(['ProbeID'], axis=1)

print("Taking log")
adata = sc.AnnData(expr.T)
sc.pp.normalize_total(adata, target_sum=1e6)
sc.pp.log1p(adata, base = 2)

expr = pd.DataFrame(adata.X)
expr = expr.T
expr.columns = df.columns[1:]

# Get gene names
genes = pd.DataFrame()
genes["ProbeID"] = df["ProbeID"]

gene_names = []
for i in genes["ProbeID"]:
    try:
        gene_names.append(ensembl_to_genesymbol[i.split(".")[0]])
    except:
        
        gene_names.append(i)

genes["Name"] = gene_names
    
expr = pd.concat([genes, expr], axis=1)
expr

Taking log


/usr/local/lib/python3.6/dist-packages/anndata/_core/anndata.py:119: ImplicitModificationWarning: Transforming to str index.
  warnings.warn("Transforming to str index.", ImplicitModificationWarning)


ProbeID           Name  GSM5048309  GSM5048310  \
0      ENSMUSG00000102693.1  4933401J01Rik    0.000000    0.000000   
1      ENSMUSG00000064842.1        Gm26206    0.000000    0.015907   
2      ENSMUSG00000051951.5           Xkr4    0.000000    0.000000   
3      ENSMUSG00000102851.1        Gm18956    0.000000    0.000000   
4      ENSMUSG00000103377.1        Gm37180    0.000000    0.000000   
...                     ...            ...         ...         ...   
55293  ENSMUSG00000095366.2        Gm21860    0.184263    0.782937   
55294  ENSMUSG00000095134.2       Mid1-ps1    0.000000    0.000000   
55295  ENSMUSG00000096768.8        Gm47283    2.806202    3.390963   
55296  ENSMUSG00000099871.1        Gm21742    0.000000    0.000000   
55297  ENSMUSG00000096850.1        Gm21748    0.000000    0.000000   

       GSM5048311  GSM5048312  GSM5048313  GSM5048314  
0        0.000000    0.000000    0.000000    0.000000  
1        0.000000    0.000000    0.000000    0.000000  
2        0.000000    0.000000    0.000000    0.000000  
3        0.000000    0.000000    0.000000    0.000000  
4        0.000000    0.000000    0.000000    0.000000  
...           ...         ...         ...         ...  
55293    0.580369    1.537862    2.356390    0.411366  
55294    0.045859    0.000000    0.000000    0.000000  
55295    3.429676    4.090979    3.746565    3.003184  
55296    0.000000    0.000000    0.000000    0.000000  
55297    0.000000    0.000000    0.000000    0.000000  

[55298 rows x 8 columns]

In [44]:
# Some Ensembl IDs point to the same gene
len(expr["Name"]) == len(hu.uniq(expr["Name"])) # False
expr.drop_duplicates(subset="Name", keep='first', inplace=True)
expr

ProbeID           Name  GSM5048309  GSM5048310  \
0      ENSMUSG00000102693.1  4933401J01Rik    0.000000    0.000000   
1      ENSMUSG00000064842.1        Gm26206    0.000000    0.015907   
2      ENSMUSG00000051951.5           Xkr4    0.000000    0.000000   
3      ENSMUSG00000102851.1        Gm18956    0.000000    0.000000   
4      ENSMUSG00000103377.1        Gm37180    0.000000    0.000000   
...                     ...            ...         ...         ...   
55293  ENSMUSG00000095366.2        Gm21860    0.184263    0.782937   
55294  ENSMUSG00000095134.2       Mid1-ps1    0.000000    0.000000   
55295  ENSMUSG00000096768.8        Gm47283    2.806202    3.390963   
55296  ENSMUSG00000099871.1        Gm21742    0.000000    0.000000   
55297  ENSMUSG00000096850.1        Gm21748    0.000000    0.000000   

       GSM5048311  GSM5048312  GSM5048313  GSM5048314  
0        0.000000    0.000000    0.000000    0.000000  
1        0.000000    0.000000    0.000000    0.000000  
2        0.000000    0.000000    0.000000    0.000000  
3        0.000000    0.000000    0.000000    0.000000  
4        0.000000    0.000000    0.000000    0.000000  
...           ...         ...         ...         ...  
55293    0.580369    1.537862    2.356390    0.411366  
55294    0.045859    0.000000    0.000000    0.000000  
55295    3.429676    4.090979    3.746565    3.003184  
55296    0.000000    0.000000    0.000000    0.000000  
55297    0.000000    0.000000    0.000000    0.000000  

[55153 rows x 8 columns]

In [45]:
path_dir = "./"
expr.to_csv(path_dir+"GSE165694-GPL17021-expr.txt", header=True, index=False,sep='\t')

In [46]:
# Build idx file

def make_idx():
    print('Starting make_idx')
    expr = path_dir+'GSE165694-GPL17021-expr.txt'

    ptr = []
    ids = []
    name = []
    desc = []
    pos = 0

    with open(expr, 'rb') as f:
        for line in f:
            if pos == 0:
                pos += len(line)
            else:
                ptr.append(pos)
                pos += len(line)
                split = line.decode("utf-8").split('\t')
                ids.append(split[0])
                name.append(split[1].split(':')[0])
                desc.append(':'.join(split[1].split(':')[1:]))
        f.close()

    with open(path_dir+'GSE165694-GPL17021-idx.txt', 'w') as f:
        f.write('ProbeID\tPtr\tName\tDescription\n')
        for i in range(len(ids)):
            f.write('{}\t{}\t{}\t{}\n'.format(ids[i], ptr[i], name[i], desc[i]))
        f.close()
    print("Done with make_idx")
    
make_idx()

Starting make_idx
Done with make_idx
